In [8]:
import numpy as np
from scipy.ndimage import gaussian_filter1d
from scipy import integrate
from scipy import stats

tinv = lambda p, df: abs(stats.t.ppf(p/2, df))

# Matplotlib configuration

In [9]:
import matplotlib.pyplot as plt
import matplotlib
from matplotlib.ticker import MultipleLocator, AutoMinorLocator
import matplotlib.colors as mcolors


matplotlib.rcParams['mathtext.fontset'] = 'custom'
matplotlib.rcParams['mathtext.rm'] = 'arial'
matplotlib.rcParams['mathtext.it'] = 'arial'
matplotlib.rcParams['mathtext.bf'] = 'arial'
matplotlib.rcParams['xtick.major.pad']='5'
matplotlib.rcParams['ytick.major.pad']='5'
matplotlib.rcParams['axes.linewidth'] = 0.75
matplotlib.rcParams['axes.axisbelow'] = True
matplotlib.rcParams['savefig.dpi'] = 1200

font = {'weight' : 'normal',
        'size'   : 16,
        'family' : "arial"}
plt.rc('font', **font)
plt.rc('axes', titlesize=font["size"])

# KBI calculation

In [10]:
Na = 6.02214e23 
units_factor = Na/1e21                              # From nm3/molecules to cm3/mol

def KBI_Integral(r, rdf):
    """
    KBI Truncating the integral at rmax.

    Args:
        r (array): vector of equispaced radii at which RDF is evaluated [units]
        rdf (array): vector of corresponding RDF values

    Returns:
        KBI (float): KBI value [units**3]
    """
    dr = r[1] - r[0]
    n = len(r)
    KBI = 4 * np.pi * integrate.cumtrapz( ( rdf - 1 ) * r**2 , r, initial = 0)
    return KBI

def KBI_Kruger(r, rdf):
    """
    KBI using Kruger correction for finite size effect.
    Kruger et al. J. Phys. Chem. Lett. 4, 235-238, 2013.

    Args:
        r (array): vector of equispaced radii at which RDF is evaluated [units]
        rdf (array): vector of corresponding RDF values

    Returns:
        KBI (float): KBI value [units**3]
    """
    dr = r[1] - r[0]
    n = len(r)
    KBI = np.zeros(n)
    for i in range(2, n):
        rvec = r[0:i]
        c = 4 * np.pi * rvec**2
        Lmax = max(rvec)      
        x = rvec/(Lmax)
        w = 1 - 3 * x / 2 + x**3 / 2
        h = rdf[0:i] - 1
        KBI[i] = np.trapz(h * c * w , x = rvec, dx = dr)
    return KBI

def KBI_extrapolation(r, KBI, x, y):
    r_inverse = 1/r
    index = (r_inverse >= x) & (r_inverse <= y)
    res = stats.linregress(r_inverse[index], KBI[index])
    G_inf_ij_value = res.intercept
    G_inf_ij_error = tinv(0.95, len(r_inverse[index])) * res.stderr
    return G_inf_ij_value, G_inf_ij_error

In [11]:
systems = [3]
combinations = ['12', '23', '11', '33', '13'] # Notation: water(1) + solute(2) + hydrotrope(3)
colors = ['#292247', '#397DB7', '#46A678', '#FDAA11', '#BA2D14']
filter_length = 20


fig, axs = plt.subplots(5, 3, figsize=(3.93701 * 3, 3.1496 * 5), dpi = 1200)

for k, ij in enumerate(combinations):       # Loop over combinations of rdf
    G_ij = []
    for l, system in enumerate(systems):    # Loop over systems
        g_ij = []
        G_Integral_ij = []
        G_Kruger_ij = []
        G_inf_ij = []
        Lx = []
        for run in range(3):                 # Loop over runs
            file = '../results/rdf/rdf_' + ij + '_' + str(system) + '_run' + str(run+1) + '.xvg'
            r, g_ij_run = np.loadtxt(file, comments=['#','@'], unpack=True)
            sigma = min(r[g_ij_run !=0])
            x, y = 1/(8*sigma), 1/(4*sigma)
            
            # Smoothing
            g_ij_run = gaussian_filter1d(g_ij_run, filter_length)
            g_ij_run = g_ij_run[r!=0]
            r = r[r!=0]

            KBI_I = KBI_Integral(r, g_ij_run) * units_factor
            KBI_K = KBI_Kruger(r, g_ij_run) * units_factor
            KBI_inf_mean, KBI_inf_std  = KBI_extrapolation(r, KBI_K, x, y)
            KBI_inf = np.random.normal(KBI_inf_mean, KBI_inf_std, 1000)

            # Save data
            g_ij.append(g_ij_run)
            G_Integral_ij.append(KBI_I)
            G_Kruger_ij.append(KBI_K)
            G_inf_ij.append(KBI_inf)


        # Average over runs
        g_ij_mean = np.mean(np.array(g_ij), axis=0)
        g_ij_std = np.std(np.array(g_ij), axis=0)
        G_Integral_ij_mean = np.mean(np.array(G_Integral_ij), axis=0)
        G_Integral_ij_std = np.std(np.array(G_Integral_ij), axis=0)
        G_Kruger_ij_mean = np.mean(np.array(G_Kruger_ij), axis=0)
        G_Kruger_ij_std = np.std(np.array(G_Kruger_ij), axis=0)
        G_inf_ij_mean = np.mean(np.array(G_inf_ij))
        G_inf_ij_std = np.std(np.array(G_inf_ij))

        # RDF - plot
        ax = axs[k, 0]
        r_max = 3
        ax.plot(r[r<r_max], g_ij_mean[r<r_max], linewidth = 1.0, c = colors[l])
        ax.fill_between(r[r<r_max], g_ij_mean[r<r_max] - g_ij_std[r<r_max], g_ij_mean[r<r_max] + g_ij_std[r<r_max], 
                        alpha=0.3, color = colors[l])
        ax.set_xlim(0, r_max)
        ax.set_xlabel(r"$r$ / nm")
        ax.set_ylabel(r"$g_{" + ij + "}(r)$ / -")

        # KBI Integral - plot
        ax = axs[k, 1]
        ax.plot(r[r<r_max], G_Integral_ij_mean[r<r_max], linewidth = 1.0, c = colors[l])
        ax.fill_between(r[r<r_max], G_Integral_ij_mean[r<r_max] - G_Integral_ij_std[r<r_max], G_Integral_ij_mean[r<r_max] + G_Integral_ij_std[r<r_max], 
                        alpha=0.3, color = colors[l])
        ax.errorbar(max(r), G_inf_ij_mean, yerr = G_inf_ij_std, fmt = 'o', color = colors[l])
        start, end = ax.get_ylim()
        ax.set_xlim(0, r_max)
        ax.set_xlabel(r"$R$ / nm")
        ax.set_ylabel(r"$G_{" + ij + "}(R)$ / $cm^{3}\cdot mol^{-1}$")
        # vertical line for x and y
        ax.axvline(1/x, color = colors[l], linestyle = '--')
        ax.axvline(1/y, color = colors[l], linestyle = '--')

        # KBI Kruger - plot
        ax = axs[k, 2]
        ax.plot(1/r, G_Kruger_ij_mean, linewidth = 1.0, c = colors[l])
        ax.fill_between(1/r, G_Kruger_ij_mean - G_Kruger_ij_std, G_Kruger_ij_mean + G_Kruger_ij_std, 
                        alpha=0.3, color = colors[l])
        ax.errorbar(0, G_inf_ij_mean, yerr = G_inf_ij_std, fmt = 'o', color = colors[l])
        ax.set_xlim(0, 2)
        ax.set_ylim(start, end)
        ax.set_xlabel(r"$R^{-1}$ / nm$^{-1}$")
        ax.set_ylabel(r"$G_{" + ij + "}(R)$ / $cm^{3}\cdot mol^{-1}$")
        ax.axvline(x, color = colors[l], linestyle = '--')
        ax.axvline(y, color = colors[l], linestyle = '--')

    print(system, ' - pair ', ij, ':', round(G_inf_ij_mean,2), '+-', round(G_inf_ij_std,2))
      
for i in range(5):
    start, end = axs[i, 0].get_ylim()
    axs[i, 0].set_ylim(0, end)

plt.subplots_adjust(left=0.15, right=0.95, bottom=0.15, top=.9, wspace=0.6, hspace=0.4)
plt.show()

3  - pair  12 : -221.54 +- 8.33
3  - pair  23 : -85.27 +- 13.91
3  - pair  11 : -2.17 +- 0.24
3  - pair  33 : -81.58 +- 0.73
3  - pair  13 : -40.96 +- 0.32
